# IBM DATA SCIENCE CAPSTONE

## Topic : Analyze the medical system in the Bay Area and make recommendations for the location of store

In [1]:
import numpy as np # library to handle data in a vectorized manner

import pandas as pd # library for data analsysis
pd.set_option('display.max_columns', None)
pd.set_option('display.max_rows', None)

import json # library to handle JSON files

#!conda install -c conda-forge geopy --yes # uncomment this line if you haven't completed the Foursquare API lab
from geopy.geocoders import Nominatim # convert an address into latitude and longitude values

import requests # library to handle requests
from pandas.io.json import json_normalize # tranform JSON file into a pandas dataframe

# Matplotlib and associated plotting modules
import matplotlib.cm as cm
import matplotlib.colors as colors

# import k-means from clustering stage
from sklearn.cluster import KMeans

!conda install -c conda-forge folium=0.5.0 --yes # uncomment this line if you haven't completed the Foursquare API lab
import folium # map rendering library

print('Libraries imported.')

Solving environment: done

## Package Plan ##

  environment location: /opt/conda/envs/Python36

  added / updated specs: 
    - folium=0.5.0


The following packages will be downloaded:

    package                    |            build
    ---------------------------|-----------------
    branca-0.4.1               |             py_0          26 KB  conda-forge
    folium-0.5.0               |             py_0          45 KB  conda-forge
    certifi-2020.4.5.1         |   py36h9f0ad1d_0         151 KB  conda-forge
    altair-4.1.0               |             py_1         614 KB  conda-forge
    ca-certificates-2020.4.5.1 |       hecc5488_0         146 KB  conda-forge
    vincent-0.4.4              |             py_1          28 KB  conda-forge
    python_abi-3.6             |          1_cp36m           4 KB  conda-forge
    openssl-1.1.1g             |       h516909a_0         2.1 MB  conda-forge
    ------------------------------------------------------------
                       

In [2]:
import types
from botocore.client import Config
import ibm_boto3

def __iter__(self): return 0

# @hidden_cell
# The following code accesses a file in your IBM Cloud Object Storage. It includes your credentials.
# You might want to remove those credentials before you share the notebook.
client_b38273abade242f8a2fb616c89a17cca = ibm_boto3.client(service_name='s3',
    ibm_api_key_id='EqSBjWuhkggq9L4x9ThAN35M-YW7sZycaSk03sZe-EdW',
    ibm_auth_endpoint="https://iam.ng.bluemix.net/oidc/token",
    config=Config(signature_version='oauth'),
    endpoint_url='https://s3-api.us-geo.objectstorage.service.networklayer.com')

body = client_b38273abade242f8a2fb616c89a17cca.get_object(Bucket='ibmcapstone-donotdelete-pr-9af35wjzhqxtqk',Key='Bay-Area-Companies-List.csv')['Body']
# add missing __iter__ method, so pandas accepts body as file-like object
if not hasattr(body, "__iter__"): body.__iter__ = types.MethodType( __iter__, body )

# If you are reading an Excel file into a pandas DataFrame, replace `read_csv` by `read_excel` in the next statement.
df_data_0 = pd.read_csv(body)
df_data_0.head()

Company Name                                               Tags  \
0       3scale           B2B Software and Services,Developer Tool   
1      8tracks                  Music,Consumer Goods and Services   
2     10 by 10       B2B Software and Services,Talent Acquisition   
3       15Five                                Employee Engagement   
4       21Tech  Real Estate and Construction,Financial Technol...   

        Location     Investors  \
0  San Francisco           NaN   
1  San Francisco           NaN   
2  San Francisco  Y Combinator   
3  San Francisco           NaN   
4       East Bay           NaN   

                                         Description                  Website  \
0    Unlock the power of your APIs (owned by RedHat)  https://www.3scale.net/   
1  8tracks is the best place to make and discover...     https://8tracks.com/   
2  We help independent recruiters and agencies ea...   https://www.10by10.io/   
3  15Five software elevates the performance and e...               15five.com   
4  Enterprise Asset Management: 21Tech has broad ...               21tech.com   

   Founded Year                                        Address        Lat  \
0        2007.0  450 Townsend St #204, San Francisco, CA 94107  37.774634   
1        2008.0          51 Sharon St, San Francisco, CA 94114  37.765227   
2        2015.0                              San Francisco, CA  37.774929   
3        2011.0       12 Gallagher Ln, San Francisco, CA 94103  37.781714   
4        1996.0         1330 Broadway #1530, Oakland, CA 94612  37.803900   

         Long Company Size Tech stack Marketing Stack  Design Stack  \
0 -122.398642        1月12日        NaN             NaN           NaN   
1 -122.429756        13-60        NaN             NaN           NaN   
2 -122.419415        1月12日        NaN             NaN           NaN   
3 -122.403236       61-150        NaN             NaN           NaN   
4 -122.270794        13-60        NaN             NaN           NaN   

   Product Stack  
0            NaN  
1            NaN  
2            NaN  
3            NaN  
4            NaN

## Data collation and feature selection

In [3]:
# Extracting the necessary columns 
df = df_data_0[['Company Name','Location','Lat','Long']]
df.head()

Company Name       Location        Lat        Long
0       3scale  San Francisco  37.774634 -122.398642
1      8tracks  San Francisco  37.765227 -122.429756
2     10 by 10  San Francisco  37.774929 -122.419415
3       15Five  San Francisco  37.781714 -122.403236
4       21Tech       East Bay  37.803900 -122.270794

In [4]:
# Renaming the columns
df.rename(columns={'Company Name':'Company','Location':'Neighbourhood','Lat':'Latitude','Long':'Longitude'}, inplace=True)
df.head()

/opt/conda/envs/Python36/lib/python3.6/site-packages/pandas/core/frame.py:4025: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: http://pandas.pydata.org/pandas-docs/stable/indexing.html#indexing-view-versus-copy
  return super(DataFrame, self).rename(**kwargs)


Company  Neighbourhood   Latitude   Longitude
0    3scale  San Francisco  37.774634 -122.398642
1   8tracks  San Francisco  37.765227 -122.429756
2  10 by 10  San Francisco  37.774929 -122.419415
3    15Five  San Francisco  37.781714 -122.403236
4    21Tech       East Bay  37.803900 -122.270794

In [5]:
df.shape

(756, 4)

In [6]:
# Since there are a lot of rows, only the first 200 rows are extracted
df = df.loc[0:200,:]
df.shape

(201, 4)

## Plotting all the company offcies in the Bay Ares on the map

In [7]:
# create map of Bay Area using latitude and longitude values
map_ba = folium.Map(location=[37.7749, -122.4194], zoom_start=12)

# add markers to map
for lat, lng, company, neighbourhood in zip(df['Latitude'], df['Longitude'], df['Company'], df['Neighbourhood']):
    label = '{}, {}'.format(company, neighbourhood)
    label = folium.Popup(label, parse_html=True)
    folium.CircleMarker(
        [lat, lng],
        radius=2,
        popup=label,
        color='blue',
        fill=True,
        fill_color='#3186cc',
        fill_opacity=0.7,
        parse_html=False).add_to(map_ba)  
    
map_ba

## Define Foursquare Credentials and Version

In [8]:
CLIENT_ID = 'O3YXUVJHIF1SCCK5OGGVHVD4SFUR0MG3QIMXOUWPZ1V45XYM' # your Foursquare ID
CLIENT_SECRET = 'DLPSSF4PRMCMXERD5ARXLWVZTJ24HKQDFZ0ATCDHPNZWPDVR' # your Foursquare Secret
VERSION = '20180605' # Foursquare API version
print('Your credentails:')
print('CLIENT_ID: ' + CLIENT_ID)
print('CLIENT_SECRET:' + CLIENT_SECRET)

Your credentails:
CLIENT_ID: O3YXUVJHIF1SCCK5OGGVHVD4SFUR0MG3QIMXOUWPZ1V45XYM
CLIENT_SECRET:DLPSSF4PRMCMXERD5ARXLWVZTJ24HKQDFZ0ATCDHPNZWPDVR


In [9]:
LIMIT = 200
radius = 1000

venues = []
for lat, long, neighborhood,company in zip(df['Latitude'], df['Longitude'], df['Neighbourhood'], df['Company']):
    
    # create the API request URL
    url = "https://api.foursquare.com/v2/venues/explore?client_id={}&client_secret={}&v={}&ll={},{}&radius={}&limit={}".format(
        CLIENT_ID,
        CLIENT_SECRET,
        VERSION,
        lat,
        long,
        radius, 
        LIMIT)
    
    # make the GET request
    results = requests.get(url).json()["response"]['groups'][0]['items']
    
    # return only relevant information for each nearby venue
    for venue in results:
        venues.append((
            neighborhood,
            company,
            lat, 
            long, 
            venue['venue']['name'], 
            venue['venue']['location']['lat'], 
            venue['venue']['location']['lng'],  
            venue['venue']['categories'][0]['name']))

In [10]:
# convert the venues list into a new DataFrame
venues_df = pd.DataFrame(venues)

# define the column names
venues_df.columns = ['Neighborhood', 'Company', 'Latitude','Longitude', 'VenueName', 'VenueLatitude', 'VenueLongitude', 'VenueCategory']

print(venues_df.shape)
venues_df.head()

(18459, 8)


Neighborhood Company   Latitude   Longitude           VenueName  \
0  San Francisco  3scale  37.774634 -122.398642      SF Flower Mart   
1  San Francisco  3scale  37.774634 -122.398642  Bay Club SF Tennis   
2  San Francisco  3scale  37.774634 -122.398642   Local Brewing Co.   
3  San Francisco  3scale  37.774634 -122.398642           MNTSTUDIO   
4  San Francisco  3scale  37.774634 -122.398642  Mission Creek Park   

   VenueLatitude  VenueLongitude         VenueCategory  
0      37.775435     -122.400913           Flower Shop  
1      37.776571     -122.397948          Tennis Court  
2      37.776550     -122.397171               Brewery  
3      37.773537     -122.402653  Gym / Fitness Center  
4      37.771538     -122.398753                  Park

In [11]:
venues_df.groupby(["Neighborhood"]).count()

Company  Latitude  Longitude  VenueName  VenueLatitude  \
Neighborhood                                                            
East Bay          2001      2001       2001       2001           2001   
New York           500       500        500        500            500   
North Bay           29        29         29         29             29   
Peninsula          968       968        968        968            968   
Sacramento          96        96         96         96             96   
San Francisco    13858     13858      13858      13858          13858   
South Bay         1007      1007       1007       1007           1007   

               VenueLongitude  VenueCategory  
Neighborhood                                  
East Bay                 2001           2001  
New York                  500            500  
North Bay                  29             29  
Peninsula                 968            968  
Sacramento                 96             96  
San Francisco           13858          13858  
South Bay                1007           1007

In [12]:
print('There are {} uniques categories.'.format(len(venues_df['VenueCategory'].unique())))

There are 365 uniques categories.


In [13]:
venues_df['VenueCategory'].unique()

array(['Flower Shop', 'Tennis Court', 'Brewery', 'Gym / Fitness Center',
       'Park', 'Vietnamese Restaurant', 'Arts & Crafts Store', 'Gym',
       'New American Restaurant', 'Winery', 'Dog Run', 'Coffee Shop',
       'Furniture / Home Store', 'Basketball Court', 'Dive Shop',
       'Pizza Place', 'Wine Shop', 'Playground', 'Sporting Goods Shop',
       'Wine Bar', 'Café', 'Organic Grocery', 'Spanish Restaurant',
       'Ethiopian Restaurant', 'Martial Arts Dojo', 'Steakhouse',
       'Dumpling Restaurant', 'Tanning Salon', 'Yoga Studio',
       'Accessories Store', 'Bar', 'Soccer Field',
       'Street Food Gathering',
       'Residential Building (Apartment / Condo)', 'Sandwich Place',
       'Food Truck', 'Poke Place', 'Southern / Soul Food Restaurant',
       'Art Gallery', 'Bakery', 'Distillery', 'Mexican Restaurant',
       'Baseball Stadium', 'Cocktail Bar', 'Spa', 'Grocery Store',
       'Mini Golf', 'Performing Arts Venue', 'Massage Studio',
       'Jewelry Store', 'Korean R

In [14]:
# Extracting the rows with Venue Category as a Store
df1 = venues_df.loc[venues_df['VenueCategory'].str.contains('Store') == True]
df1.head()

Neighborhood Company   Latitude   Longitude           VenueName  \
6   San Francisco  3scale  37.774634 -122.398642          Fantastico   
13  San Francisco  3scale  37.774634 -122.398642        Room & Board   
35  San Francisco  3scale  37.774634 -122.398642          Wood Thumb   
61  San Francisco  3scale  37.774634 -122.398642  Whole Foods Market   
62  San Francisco  3scale  37.774634 -122.398642      H.D. Buttercup   

    VenueLatitude  VenueLongitude           VenueCategory  
6       37.775551     -122.401576     Arts & Crafts Store  
13      37.772262     -122.401723  Furniture / Home Store  
35      37.779557     -122.402547       Accessories Store  
61      37.781224     -122.400080           Grocery Store  
62      37.777490     -122.394582  Furniture / Home Store

In [15]:
# Sorting the rows by Venue Category
df1.sort_values(by=['VenueCategory'],inplace=True)

/opt/conda/envs/Python36/lib/python3.6/site-packages/ipykernel/__main__.py:2: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: http://pandas.pydata.org/pandas-docs/stable/indexing.html#indexing-view-versus-copy
  from ipykernel import kernelapp as app


In [16]:
df1.head()

Neighborhood        Company   Latitude   Longitude          VenueName  \
1743   San Francisco          Adobe  37.771206 -122.401662         Wood Thumb   
1510       Peninsula  Adecco Group   37.635000 -122.424555           Claire's   
14306  San Francisco           Coda  37.776597 -122.391949         Wood Thumb   
8596   San Francisco      BloomThat  37.751824 -122.389362  Rickshaw Bagworks   
13980       East Bay    CloudFabrix  37.690223 -121.930334           Claire's   

       VenueLatitude  VenueLongitude      VenueCategory  
1743       37.779557     -122.402547  Accessories Store  
1510       37.636509     -122.417482  Accessories Store  
14306      37.779557     -122.402547  Accessories Store  
8596       37.757908     -122.390539  Accessories Store  
13980      37.694600     -121.928516  Accessories Store

In [17]:
# onehot encoding
onehot = pd.get_dummies(df1['VenueCategory'],prefix='',prefix_sep='')
onehot.head()

Accessories Store  Arts & Crafts Store  Beer Store  Big Box Store  \
1743                   1                    0           0              0   
1510                   1                    0           0              0   
14306                  1                    0           0              0   
8596                   1                    0           0              0   
13980                  1                    0           0              0   

       Camera Store  Candy Store  Clothing Store  Convenience Store  \
1743              0            0               0                  0   
1510              0            0               0                  0   
14306             0            0               0                  0   
8596              0            0               0                  0   
13980             0            0               0                  0   

       Department Store  Discount Store  Electronics Store  \
1743                  0               0                  0   
1510                  0               0                  0   
14306                 0               0                  0   
8596                  0               0                  0   
13980                 0               0                  0   

       Furniture / Home Store  Grocery Store  Hardware Store  \
1743                        0              0               0   
1510                        0              0               0   
14306                       0              0               0   
8596                        0              0               0   
13980                       0              0               0   

       Herbs & Spices Store  Jewelry Store  Kids Store  Kitchen Supply Store  \
1743                      0              0           0                     0   
1510                      0              0           0                     0   
14306                     0              0           0                     0   
8596                      0              0           0                     0   
13980                     0              0           0                     0   

       Lingerie Store  Liquor Store  Mattress Store  Medical Supply Store  \
1743                0             0               0                     0   
1510                0             0               0                     0   
14306               0             0               0                     0   
8596                0             0               0                     0   
13980               0             0               0                     0   

       Men's Store  Music Store  Outdoor Supply Store  \
1743             0            0                     0   
1510             0            0                     0   
14306            0            0                     0   
8596             0            0                     0   
13980            0            0                     0   

       Paper / Office Supplies Store  Pet Store  Shipping Store  Shoe Store  \
1743                               0          0               0           0   
1510                               0          0               0           0   
14306                              0          0               0           0   
8596                               0          0               0           0   
13980                              0          0               0           0   

       Thrift / Vintage Store  Toy / Game Store  Video Game Store  \
1743                        0                 0                 0   
1510                        0                 0                 0   
14306                       0                 0                 0   
8596                        0                 0                 0   
13980                       0                 0                 0   

       Video Store  Warehouse Store  Women's Store  
1743             0                0              0  
1510             0                0              0  
14306            0           

In [18]:
# Creating a copy of dataframe
df2 = df1
df2.head()

Neighborhood        Company   Latitude   Longitude          VenueName  \
1743   San Francisco          Adobe  37.771206 -122.401662         Wood Thumb   
1510       Peninsula  Adecco Group   37.635000 -122.424555           Claire's   
14306  San Francisco           Coda  37.776597 -122.391949         Wood Thumb   
8596   San Francisco      BloomThat  37.751824 -122.389362  Rickshaw Bagworks   
13980       East Bay    CloudFabrix  37.690223 -121.930334           Claire's   

       VenueLatitude  VenueLongitude      VenueCategory  
1743       37.779557     -122.402547  Accessories Store  
1510       37.636509     -122.417482  Accessories Store  
14306      37.779557     -122.402547  Accessories Store  
8596       37.757908     -122.390539  Accessories Store  
13980      37.694600     -121.928516  Accessories Store

In [19]:
# Merging the dummy variables with the original dataframe
df3 = pd.merge(df2,onehot,on=df2.index)
df3.head(50)

key_0   Neighborhood                               Company   Latitude  \
0    1743  San Francisco                                 Adobe  37.771206   
1    1510      Peninsula                         Adecco Group   37.635000   
2   14306  San Francisco                                  Coda  37.776597   
3    8596  San Francisco                             BloomThat  37.751824   
4   13980       East Bay                           CloudFabrix  37.690223   
5   13967       East Bay                           CloudFabrix  37.690223   
6    5291  San Francisco                             Apptimize  37.776860   
7   13768  San Francisco                              Cloud4Wi  37.781278   
8   13755  San Francisco                   Climate Corporation  37.785067   
9    5659       East Bay                               Art.com  37.839364   
10  13209  San Francisco                              Clearbit  37.778035   
11  12748  San Francisco                        Circle Medical  37.782141   
12   5666       East Bay                               Art.com  37.839364   
13   5668       East Bay                               Art.com  37.839364   
14  11888  San Francisco                                Castle  37.776142   
15   5962  San Francisco                            Atrium LTS  37.778262   
16  11647  San Francisco                      Carrot Fertility  37.779816   
17  11422  San Francisco                           Capital One  37.785067   
18   8237       East Bay                     Blackhawk Network  37.695488   
19   9027  San Francisco                                  Bolt  37.776857   
20   8235       East Bay                     Blackhawk Network  37.695488   
21   8211       East Bay                     Blackhawk Network  37.695488   
22   9350  San Francisco  Bradfield School of Computer Science  37.778974   
23   9741  San Francisco                               Brigade  37.780864   
24   4364  San Francisco                             AngelList  37.796759   
25   1106  San Francisco                              Abstract  37.756034   
26   6729  San Francisco                                  Bebo  37.781274   
27  10773     Sacramento                               Bukwild  38.582053   
28  10967  San Francisco                          Cadre Talent  37.800405   
29  11129  San Francisco                              Campsyte  37.779515   
30   6424  San Francisco                            BabyCenter  37.777601   
31  11292  San Francisco                             Capgemini  37.779352   
32  10450  San Francisco                               Bugsnag  37.778197   
33  14970  San Francisco                     Collective Health  37.776105   
34  13986       East Bay                           CloudFabrix  37.690223   
35   8701  San Francisco                              BlueCrew  37.772775   
36   2349  San Francisco                              Affinity  37.796981   
37   4227  San Francisco                                Angaza  37.782333   
38  17366  San Francisco                            Demandbase  37.784558   
39  16903  San Francisco                               DataFox  37.782493   
40   2911  San Francisco                                  AKQA  37.782707   
41  18077  San Francisco                           Divvy Homes  37.784547   
42    305  San Francisco                                15Five  37.781714   
43   1848  San Francisco                                AdRoll  37.760419   
44   3365  San Francisco                                 Alloy  37.780521   
45   3639  San Francisco                          Always Hired  37.782143   
46  16370  San Francisco                           Crunchyroll  37.783535   
47   2029  San Francisco                       Advent Software  37.771704   
48  18348  San Francisco                                Docker  37.780151   
49   3912      South Bay                            Ambient.ai  37.447222   

     Longitude              VenueName  VenueLatitude  VenueLongitude  \
0  -

In [20]:
# drop column key_0
df3.drop(['key_0'],axis=1,inplace=True)
df3.head()

Neighborhood        Company   Latitude   Longitude          VenueName  \
0  San Francisco          Adobe  37.771206 -122.401662         Wood Thumb   
1      Peninsula  Adecco Group   37.635000 -122.424555           Claire's   
2  San Francisco           Coda  37.776597 -122.391949         Wood Thumb   
3  San Francisco      BloomThat  37.751824 -122.389362  Rickshaw Bagworks   
4       East Bay    CloudFabrix  37.690223 -121.930334           Claire's   

   VenueLatitude  VenueLongitude      VenueCategory  Accessories Store  \
0      37.779557     -122.402547  Accessories Store                  1   
1      37.636509     -122.417482  Accessories Store                  1   
2      37.779557     -122.402547  Accessories Store                  1   
3      37.757908     -122.390539  Accessories Store                  1   
4      37.694600     -121.928516  Accessories Store                  1   

   Arts & Crafts Store  Beer Store  Big Box Store  Camera Store  Candy Store  \
0                    0           0              0             0            0   
1                    0           0              0             0            0   
2                    0           0              0             0            0   
3                    0           0              0             0            0   
4                    0           0              0             0            0   

   Clothing Store  Convenience Store  Department Store  Discount Store  \
0               0                  0                 0               0   
1               0                  0                 0               0   
2               0                  0                 0               0   
3               0                  0                 0               0   
4               0                  0                 0               0   

   Electronics Store  Furniture / Home Store  Grocery Store  Hardware Store  \
0                  0                       0              0               0   
1                  0                       0              0               0   
2                  0                       0              0               0   
3                  0                       0              0               0   
4                  0                       0              0               0   

   Herbs & Spices Store  Jewelry Store  Kids Store  Kitchen Supply Store  \
0                     0              0           0                     0   
1                     0              0           0                     0   
2                     0              0           0                     0   
3                     0              0           0                     0   
4                     0              0           0                     0   

   Lingerie Store  Liquor Store  Mattress Store  Medical Supply Store  \
0               0             0               0                     0   
1               0             0               0                     0   
2               0             0               0                     0   
3               0             0               0                     0   
4               0             0               0                     0   

   Men's Store  Music Store  Outdoor Supply Store  \
0            0            0                     0   
1            0            0                     0   
2            0            0                     0   
3            0            0                     0   
4            0            0                     0   

   Paper / Office Supplies Store  Pet Store  Shipping Store  Shoe Store  \
0                              0          0               0           0   
1                              0          0               0           0   
2                              0          0               0           0   
3                              0          0               0           0   
4                              0          0               0           0   

   Thrift / Vintage Store  To

In [21]:
#leave only columns of store
group_clustering = df3.drop(['Neighborhood','Company','Latitude','Longitude','VenueName','VenueLatitude','VenueLongitude','VenueCategory'],axis=1)
group_clustering.head()

Accessories Store  Arts & Crafts Store  Beer Store  Big Box Store  \
0                  1                    0           0              0   
1                  1                    0           0              0   
2                  1                    0           0              0   
3                  1                    0           0              0   
4                  1                    0           0              0   

   Camera Store  Candy Store  Clothing Store  Convenience Store  \
0             0            0               0                  0   
1             0            0               0                  0   
2             0            0               0                  0   
3             0            0               0                  0   
4             0            0               0                  0   

   Department Store  Discount Store  Electronics Store  \
0                 0               0                  0   
1                 0               0                  0   
2                 0               0                  0   
3                 0               0                  0   
4                 0               0                  0   

   Furniture / Home Store  Grocery Store  Hardware Store  \
0                       0              0               0   
1                       0              0               0   
2                       0              0               0   
3                       0              0               0   
4                       0              0               0   

   Herbs & Spices Store  Jewelry Store  Kids Store  Kitchen Supply Store  \
0                     0              0           0                     0   
1                     0              0           0                     0   
2                     0              0           0                     0   
3                     0              0           0                     0   
4                     0              0           0                     0   

   Lingerie Store  Liquor Store  Mattress Store  Medical Supply Store  \
0               0             0               0                     0   
1               0             0               0                     0   
2               0             0               0                     0   
3               0             0               0                     0   
4               0             0               0                     0   

   Men's Store  Music Store  Outdoor Supply Store  \
0            0            0                     0   
1            0            0                     0   
2            0            0                     0   
3            0            0                     0   
4            0            0                     0   

   Paper / Office Supplies Store  Pet Store  Shipping Store  Shoe Store  \
0                              0          0               0           0   
1                              0          0               0           0   
2                              0          0               0           0   
3                              0          0               0           0   
4                              0          0               0           0   

   Thrift / Vintage Store  Toy / Game Store  Video Game Store  Video Store  \
0                       0                 0                 0            0   
1                       0                 0                 0            0   
2                       0                 0                 0            0   
3                       0                 0                 0            0   
4                       0                 0                 0            0   

   Warehouse Store  Women's Store  
0                0              0  
1                0              0  
2                0              0  
3                0              0  
4                0              0

## Using KMeans Machine Learning Algorithm for the clustering of the stores near the bay area companies

In [22]:
# set number of clusters
k = 5
# run k-means clustering
kmeans = KMeans(n_clusters=k,random_state=0).fit(group_clustering)
# check cluster labels generated for each row in the dataframe
kmeans.labels_[0:10]

array([0, 0, 0, 0, 0, 0, 0, 0, 0, 0], dtype=int32)

In [23]:
df3.head()

Neighborhood        Company   Latitude   Longitude          VenueName  \
0  San Francisco          Adobe  37.771206 -122.401662         Wood Thumb   
1      Peninsula  Adecco Group   37.635000 -122.424555           Claire's   
2  San Francisco           Coda  37.776597 -122.391949         Wood Thumb   
3  San Francisco      BloomThat  37.751824 -122.389362  Rickshaw Bagworks   
4       East Bay    CloudFabrix  37.690223 -121.930334           Claire's   

   VenueLatitude  VenueLongitude      VenueCategory  Accessories Store  \
0      37.779557     -122.402547  Accessories Store                  1   
1      37.636509     -122.417482  Accessories Store                  1   
2      37.779557     -122.402547  Accessories Store                  1   
3      37.757908     -122.390539  Accessories Store                  1   
4      37.694600     -121.928516  Accessories Store                  1   

   Arts & Crafts Store  Beer Store  Big Box Store  Camera Store  Candy Store  \
0                    0           0              0             0            0   
1                    0           0              0             0            0   
2                    0           0              0             0            0   
3                    0           0              0             0            0   
4                    0           0              0             0            0   

   Clothing Store  Convenience Store  Department Store  Discount Store  \
0               0                  0                 0               0   
1               0                  0                 0               0   
2               0                  0                 0               0   
3               0                  0                 0               0   
4               0                  0                 0               0   

   Electronics Store  Furniture / Home Store  Grocery Store  Hardware Store  \
0                  0                       0              0               0   
1                  0                       0              0               0   
2                  0                       0              0               0   
3                  0                       0              0               0   
4                  0                       0              0               0   

   Herbs & Spices Store  Jewelry Store  Kids Store  Kitchen Supply Store  \
0                     0              0           0                     0   
1                     0              0           0                     0   
2                     0              0           0                     0   
3                     0              0           0                     0   
4                     0              0           0                     0   

   Lingerie Store  Liquor Store  Mattress Store  Medical Supply Store  \
0               0             0               0                     0   
1               0             0               0                     0   
2               0             0               0                     0   
3               0             0               0                     0   
4               0             0               0                     0   

   Men's Store  Music Store  Outdoor Supply Store  \
0            0            0                     0   
1            0            0                     0   
2            0            0                     0   
3            0            0                     0   
4            0            0                     0   

   Paper / Office Supplies Store  Pet Store  Shipping Store  Shoe Store  \
0                              0          0               0           0   
1                              0          0               0           0   
2                              0          0               0           0   
3                              0          0               0           0   
4                              0          0               0           0   

   Thrift / Vintage Store  To

In [24]:
# add clustering labels
df3.insert(0,'ClusterLabels',kmeans.labels_)

## Creating the map of all the stores

In [25]:
# create map
map_clusters = folium.Map(location=[37.7749, -122.4194], zoom_start=11)

# set color scheme for the clusters
x = np.arange(k)
ys = [i + x + (i*x)**2 for i in range(k)]
colors_array = cm.rainbow(np.linspace(0, 1, len(ys)))
rainbow = [colors.rgb2hex(i) for i in colors_array]

# add markers to the map
markers_colors = []
for lat, lon, name, cat, cluster in zip(df3['VenueLatitude'], df3['VenueLongitude'], df3['VenueName'],df3['VenueCategory'], df3['ClusterLabels']):
    label = folium.Popup(name +','+ cat + ' Cluster ' + str(cluster), parse_html=True)
    folium.CircleMarker(
        [lat, lon],
        radius=4,
        popup=label,
        color=rainbow[cluster-1],
        fill=True,
        fill_color=rainbow[cluster-1],
        fill_opacity=0.7).add_to(map_clusters)
    
# The clusters in the map shows different types of stores on the basis of different attributes
for lat, lng, company, neighbourhood in zip(df3['Latitude'], df3['Longitude'], df3['Company'], df3['Neighborhood']):
    label = '{}, {}'.format(company, neighbourhood)
    label = folium.Popup(label, parse_html=True)
    folium.CircleMarker(
        [lat, lng],
        radius=5,
        popup=label,
        color='blue',
        fill=True,
        fill_color='#3186cc',
        fill_opacity=0.7,
        parse_html=False).add_to(map_clusters) 
    
map_clusters

## Examining Clusters 

In [27]:
#The Cluster 0 is shown in Red Colour
cluster0 = df3.loc[df3['ClusterLabels'] == 0, df3.columns[[1] + list(range(5, df3.shape[1]))]]
cluster0['VenueCategory'].value_counts()

Arts & Crafts Store              109
Furniture / Home Store           104
Electronics Store                101
Jewelry Store                     99
Accessories Store                 55
Kitchen Supply Store              52
Pet Store                         44
Mattress Store                    24
Shipping Store                    23
Convenience Store                 22
Toy / Game Store                  16
Candy Store                       15
Camera Store                      13
Department Store                  11
Women's Store                      9
Lingerie Store                     9
Kids Store                         8
Hardware Store                     8
Paper / Office Supplies Store      7
Music Store                        7
Shoe Store                         6
Thrift / Vintage Store             6
Discount Store                     5
Big Box Store                      5
Video Store                        4
Video Game Store                   3
Beer Store                         3
O

In [28]:
#The Cluster 1 is shown in Purple Colour
cluster1 = df3.loc[df3['ClusterLabels'] == 1, df3.columns[[1] + list(range(5, df3.shape[1]))]]
cluster1['VenueCategory'].value_counts()

Clothing Store    195
Name: VenueCategory, dtype: int64

In [29]:
#The Cluster 2 is shown in Light Blue Color
cluster2 = df3.loc[df3['ClusterLabels'] == 2, df3.columns[[1] + list(range(5, df3.shape[1]))]]
cluster2['VenueCategory'].value_counts()

Men's Store    147
Name: VenueCategory, dtype: int64

In [30]:
#The Cluster 3 is shown in Green color
cluster3 = df3.loc[df3['ClusterLabels'] == 3, df3.columns[[1] + list(range(5, df3.shape[1]))]]
cluster3['VenueCategory'].value_counts()

Grocery Store    224
Name: VenueCategory, dtype: int64

In [31]:
#The Cluster 4 is shown in Orange color
cluster4 = df3.loc[df3['ClusterLabels'] == 4, df3.columns[[1] + list(range(5, df3.shape[1]))]]
cluster4['VenueCategory'].value_counts()

Liquor Store    120
Name: VenueCategory, dtype: int64

## observations
### 1.In general, the red represents Electronics Store, Arts & Crafts Store, Furniture / Home Store etc. is the main part, which is also because the base of these stores is relatively large, but surprisingly there are only 2 such stores near Daily Kos, East Bay. So, it would be a wise decision to open an Electronics Store here.
### 2.Similarly, the numbers of purple point and light blue points represents clothing store and men’s store are 0 near DNAnexus, South Bay. Therefore, if you start a clothing store or men’s store then nearly all the customers working near DNAnexus, South Bay will come here.
### 3.We can conclude that a better choice to open stores near Cloudbees, South Bay is Grocery Store.
### 4.We can find the orange points (Liquor Store) mostly located near San Francisco and Peninsula. So, the other places are all good choices.